In [51]:
# Imports
import numpy as np
import pandas as pd
import requests

# Fin Data Sources
import yfinance as yf
import pandas_datareader as pdr

# Data viz
import plotly.graph_objs as go
import plotly.express as px

import time
from datetime import datetime
from datetime import date
from datetime import timedelta

# for graphs
import matplotlib.pyplot as plt

In [3]:
# Get IPOs data from the Web
headers = {
    'User-Agent': 'Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/58.0.3029.110 Safari/537.3',
}

url = "https://stockanalysis.com/ipos/2023/"
response = requests.get(url, headers=headers)

ipo_dfs = pd.read_html(response.text)

C:\Users\mmo990\AppData\Local\Temp\ipykernel_1384\546175574.py:9: FutureWarning: Passing literal html to 'read_html' is deprecated and will be removed in a future version. To read from a literal string, wrap it in a 'StringIO' object.
  ipo_dfs = pd.read_html(response.text)


In [4]:
ipos_2023 = ipo_dfs[0]
ipos_2023.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 154 entries, 0 to 153
Data columns (total 6 columns):
 #   Column        Non-Null Count  Dtype 
---  ------        --------------  ----- 
 0   IPO Date      154 non-null    object
 1   Symbol        154 non-null    object
 2   Company Name  154 non-null    object
 3   IPO Price     154 non-null    object
 4   Current       154 non-null    object
 5   Return        154 non-null    object
dtypes: object(6)
memory usage: 7.3+ KB


In [5]:
# Get IPOs data from 2024

url = "https://stockanalysis.com/ipos/2024/"
response = requests.get(url, headers=headers)

ipo_dfs = pd.read_html(response.text)

ipos_2024 = ipo_dfs[0]
ipos_2024.info()    


<class 'pandas.core.frame.DataFrame'>
RangeIndex: 64 entries, 0 to 63
Data columns (total 6 columns):
 #   Column        Non-Null Count  Dtype 
---  ------        --------------  ----- 
 0   IPO Date      64 non-null     object
 1   Symbol        64 non-null     object
 2   Company Name  64 non-null     object
 3   IPO Price     64 non-null     object
 4   Current       64 non-null     object
 5   Return        64 non-null     object
dtypes: object(6)
memory usage: 3.1+ KB


C:\Users\mmo990\AppData\Local\Temp\ipykernel_1384\3406007452.py:6: FutureWarning: Passing literal html to 'read_html' is deprecated and will be removed in a future version. To read from a literal string, wrap it in a 'StringIO' object.
  ipo_dfs = pd.read_html(response.text)


In [6]:
# "stacking dataframes"
# pd.concat() is used to concatenate the DataFrames vertically.
# The ignore_index=True parameter ensures that the resulting DataFrame has a new index,
# ignoring the original indices of the input DataFrames.
# The stacked_df now contains the concatenated DataFrame.

stacked_ipos_df = pd.concat([ipos_2024, ipos_2023], ignore_index=True)
stacked_ipos_df.head(1)   

IPO Date Symbol          Company Name IPO Price Current  Return
0  May 1, 2024    VIK  Viking Holdings Ltd.    $24.00  $28.94  20.58%

In [7]:
# Need to convert everything to a proper type (date, str, int, float, etc.)
stacked_ipos_df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 218 entries, 0 to 217
Data columns (total 6 columns):
 #   Column        Non-Null Count  Dtype 
---  ------        --------------  ----- 
 0   IPO Date      218 non-null    object
 1   Symbol        218 non-null    object
 2   Company Name  218 non-null    object
 3   IPO Price     218 non-null    object
 4   Current       218 non-null    object
 5   Return        218 non-null    object
dtypes: object(6)
memory usage: 10.3+ KB


In [15]:
# Convert to datetime
stacked_ipos_df['IPO Date'] = pd.to_datetime(stacked_ipos_df['IPO Date'], format='%b %d, %Y')

Empty DataFrame
Columns: [IPO Date, Symbol, Company Name, IPO Price, Current, Return]
Index: []

In [20]:
# Problem --> not always the columns are filled
missing_prices_df = stacked_ipos_df[stacked_ipos_df['IPO Price'].astype(str).str.find('-') >= 0]
missing_prices_df

Empty DataFrame
Columns: [IPO Date, Symbol, Company Name, IPO Price, Current, Return]
Index: []

In [25]:
#     : pd.to_numeric() function call, which will convert problematic values to NaN.
#     otherwise you'll get a ValueError: Unable to parse string "-" at position 9
stacked_ipos_df['IPO Price'] = pd.to_numeric(stacked_ipos_df['IPO Price'].str.replace('$', ''), errors='coerce')


In [23]:
# Convert "Current" column
stacked_ipos_df['Current'] = pd.to_numeric(stacked_ipos_df['Current'].str.replace('$', ''), errors='coerce')

# Convert 'Return' to numeric format (percentage)
stacked_ipos_df['Return'] = pd.to_numeric(stacked_ipos_df['Return'].str.replace('%', ''), errors='coerce') / 100

In [26]:
# Correctly applied transformations with 'defensive' techniques, but now not all are non-null
stacked_ipos_df.info()
    

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 218 entries, 0 to 217
Data columns (total 6 columns):
 #   Column        Non-Null Count  Dtype         
---  ------        --------------  -----         
 0   IPO Date      218 non-null    datetime64[ns]
 1   Symbol        218 non-null    object        
 2   Company Name  218 non-null    object        
 3   IPO Price     218 non-null    float64       
 4   Current       218 non-null    float64       
 5   Return        218 non-null    float64       
dtypes: datetime64[ns](1), float64(3), object(2)
memory usage: 10.3+ KB


In [27]:
# Check for NULLs
stacked_ipos_df.isnull().sum()

IPO Date        0
Symbol          0
Company Name    0
IPO Price       0
Current         0
Return          0
dtype: int64

In [29]:
# Generate a new field for price increase
stacked_ipos_df['Price Increase'] = stacked_ipos_df['Current'] - stacked_ipos_df['IPO Price']
stacked_ipos_df.head(1)

IPO Date Symbol          Company Name  IPO Price  Current  Return  \
0 2024-05-01    VIK  Viking Holdings Ltd.       24.0    28.94  0.2058   

   Price Increase  
0            4.94

In [30]:
# Descriptive Analytics of a dataset
stacked_ipos_df.describe()

IPO Date   IPO Price     Current      Return  \
count                            218  218.000000  218.000000  218.000000   
mean   2023-09-08 03:44:35.229357824   11.060229   11.197844   -0.206825   
min              2023-01-13 00:00:00    2.500000    0.000000   -0.999600   
25%              2023-04-20 00:00:00    4.000000    1.275000   -0.733025   
50%              2023-09-14 12:00:00    8.000000    5.505000   -0.229250   
75%              2024-01-24 18:00:00   13.750000   10.827500    0.060750   
max              2024-05-01 00:00:00   92.000000  120.330000    2.500000   
std                              NaN   11.245650   17.503495    0.647434   

       Price Increase  
count      218.000000  
mean         0.137615  
min        -21.260000  
25%         -3.670000  
50%         -1.645000  
75%          0.567500  
max         55.980000  
std          9.396215

In [31]:
# Some visualisation: bar chart using Plotly Express
# Truncate to the first day in the month - for Bar names
stacked_ipos_df['Date_monthly'] = stacked_ipos_df['IPO Date'].dt.to_period('M').dt.to_timestamp()

# Count the number of deals for each month and year
monthly_deals = stacked_ipos_df['Date_monthly'].value_counts().reset_index().sort_values(by='Date_monthly')
monthly_deals.columns = ['Date_monthly', 'Number of Deals']

# Plotting the bar chart using Plotly Express
fig = px.bar(monthly_deals,
             x='Date_monthly',
             y='Number of Deals',
             labels={'Month_Year': 'Month and Year', 'Number of Deals': 'Number of Deals'},
             title='Number of IPO Deals per Month and Year',
             text='Number of Deals'
             )
fig.update_traces(textposition='outside', # Position the text outside the bars
                  textfont=dict(color='black',size=14), # Adjust the font size of the text
                  )
fig.update_layout(title_x=0.5) # Center the title

fig.show()

c:\Users\mmo990\AppData\Local\anaconda3\envs\investpythonzoomcamp\Lib\site-packages\_plotly_utils\basevalidators.py:106: FutureWarning: The behavior of DatetimeProperties.to_pydatetime is deprecated, in a future version this will return a Series containing python datetime objects instead of an ndarray. To retain the old behavior, call `np.array` on the result
  v = v.dt.to_pydatetime()


# What's the total sum ($m) of 2023 filings that happened on Fridays?

In [113]:
# Get IPOs filings data from 2023
url = "https://stockanalysis.com/ipos/filings/"
response = requests.get(url, headers=headers)

ipo_filing = pd.read_html(response.text)

ipos_filing = ipo_filing[0]
ipos_filing.info()    

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 325 entries, 0 to 324
Data columns (total 5 columns):
 #   Column          Non-Null Count  Dtype 
---  ------          --------------  ----- 
 0   Filing Date     325 non-null    object
 1   Symbol          325 non-null    object
 2   Company Name    325 non-null    object
 3   Price Range     325 non-null    object
 4   Shares Offered  325 non-null    object
dtypes: object(5)
memory usage: 12.8+ KB


C:\Users\mmo990\AppData\Local\Temp\ipykernel_1384\3790124393.py:5: FutureWarning:

Passing literal html to 'read_html' is deprecated and will be removed in a future version. To read from a literal string, wrap it in a 'StringIO' object.



In [114]:
# Convert Filing Date to datetime
ipos_filing['Filing Date'] = pd.to_datetime(ipos_filing['Filing Date'], format='%b %d, %Y')

In [115]:
# Select only data from 2023
ipos_filing = ipos_filing[(ipos_filing['Filing Date'] > '2023-01-01') & (ipos_filing['Filing Date'] < '2023-12-31')]

In [116]:
# Check "Sahres Offered" for NaN entries '-' 
# Problem --> not always the columns are filled
missing_sharesn_df = ipos_filing[ipos_filing['Shares Offered'].astype(str).str.find('-') >= 0]
missing_sharesn_df

Filing Date Symbol                                       Company Name  \
51   2023-12-29   EPSM                          Epsium Enterprise Limited   
54   2023-12-22   CHLW    Chun Hui Le Wan International Holding Group Ltd   
55   2023-12-22   LZMH                     LZ Technology Holdings Limited   
58   2023-12-20    AHL                   Aspen Insurance Holdings Limited   
60   2023-12-15    GIT        Going International Holding Company Limited   
61   2023-12-11    EIL                             E I L Holdings Limited   
64   2023-12-07    HOS                   Hornbeck Offshore Services, Inc.   
66   2023-12-06   WDQY           Wangdiqiyuan International Holdings Ltd.   
67   2023-11-29   HHGJ                             Concord Health Limited   
71   2023-11-09   QMIX                       QMIS TBS Capital Group Corp.   
74   2023-11-08    JFY            Jiufuyuan Biotechnology Company Limited   
81   2023-10-30   FONG                           Aibafang Group CO., Ltd.   
88   2023-10-16    WAY                              Waystar Holding Corp.   
94   2023-10-04   ROTR                                    PHI Group, Inc.   
95   2023-10-03   GRDN                   Guardian Pharmacy Services, Inc.   
105  2023-08-31   TYGJ  American Tuoyuan International Securities Grou...   
107  2023-08-23   HXSZ                Hongxu Shangzeng Global Holding Ltd   
109  2023-08-11   ZXTY                        Zhongxing Holding Group Ltd   
112  2023-08-08   ZDYM             Zhiding Yuemei Technology Co., Limited   
113  2023-08-04    JZL                       Jizhilong Holding Group Ltd.   
117  2023-07-26   HAND  Hand in Hand Metaverse Marriage Technnology Co...   
122  2023-07-05    LGM                                     Sixgomeow Ltd.   
128  2023-06-20   JDRR                        F3 Platform Biologics, Inc.   
142  2023-03-30   HUHU                  HUHUTECH International Group Inc.   
143  2023-03-24   USEE                       USEE Electronic Commerce Ltd   
148  2023-03-02   DAZS     Da Ai Zhi Shui International Holding Group Ltd   
155  2023-02-14   IAMR           Medical Industries of the Americas, Inc.   
159  2023-02-09   EPWK                                 EPWK Holdings Ltd.   
160  2023-02-08    ZBJ                              ZBJ Finance Group Ltd   
161  2023-02-07    YZH            Yuezhonghui International Holdings Ltd.   
164  2023-01-23   RPET                         New Ruipeng Pet Group Inc.   

    Price Range Shares Offered  
51            -              -  
54            -              -  
55            -              -  
58            -              -  
60            -              -  
61            -              -  
64            -              -  
66            -              -  
67        $4.00              -  
71            -              -  
74        $5.00              -  
81            -              -  
88            -              -  
94            -              -  
95            -              -  
105           -              -  
107           -              -  
109           -              -  
112       $5.00              -  
113           -              -  
117           -              -  
122       $5.00              -  
128           -              -  
142           -              -  
143           -              -  
148           -              -  
155           -              -  
159           -              -  
160           -              -  
161           -              -  
164           -              -

In [121]:
# Replace '-' with nan
ipos_filing['Shares Offered'] = ipos_filing['Shares Offered'].replace('-', np.nan)

C:\Users\mmo990\AppData\Local\Temp\ipykernel_1384\3013741824.py:2: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



In [122]:
# Convert "Sares Offered" column to float
ipos_filing['Shares Offered'] = pd.to_numeric(ipos_filing['Shares Offered'], errors='coerce')
ipos_filing.isnull().sum()

C:\Users\mmo990\AppData\Local\Temp\ipykernel_1384\1042829632.py:2: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



Filing Date        0
Symbol             0
Company Name       0
Price Range        0
Shares Offered    31
dtype: int64

In [127]:
# Function to calculate average price
def calculate_avg_price(price_range):
    if pd.isna(price_range) or price_range.strip() == ''or price_range.strip() == '-':
        return np.nan
    elif '-' in price_range:
        price_range = price_range.replace('$', '')
        prices = price_range.split(' - ')
        return (float(prices[0]) + float(prices[1])) / 2
    else:
        price_range = price_range.replace('$', '')
        return float(price_range)

# Apply the function to create the 'Avg_price' field
ipos_filing['Avg_Price'] = ipos_filing['Price Range'].apply(calculate_avg_price)


C:\Users\mmo990\AppData\Local\Temp\ipykernel_1384\1809023371.py:17: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



In [130]:
# Define a new column 'Shares_offered_value' which equals 'Shares Offered'*'Avg_Price' 

# Define a function to calculate Shares_offered_value
def calculate_shares_offered_value(row):
    shares_offered = row['Shares Offered']
    avg_price = row['Avg_Price']
    if pd.isna(shares_offered) or pd.isna(avg_price):
        return np.nan
    else:
        return shares_offered * avg_price

# Apply the function to create the 'Shares_offered_value' column
ipos_filing['Shares_offered_value'] = ipos_filing.apply(calculate_shares_offered_value, axis=1)


C:\Users\mmo990\AppData\Local\Temp\ipykernel_1384\4175900986.py:13: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



In [145]:
# Find the total sum in $m (millions of USD, closest INTEGER number) for all filings during 2023, which happened on Fridays 
friday_data = ipos_filing[ipos_filing['Filing Date'].dt.dayofweek == 4]

friday_data = friday_data.dropna(subset='Shares_offered_value', how='any')

# Check there is 25 records that are not nan
len(friday_data)

sum_fridays_23 = round(friday_data['Shares_offered_value'].sum() * 10**-6)
print('The total sum for all fillings on a Friday in 2023 is {} $millions'.format(sum_fridays_23))

The total sum for all fillings on a Friday in 2023 is 286 $millions


# Question 2

In [3]:
# Get IPOs data from the Web for 2023
headers = {
    'User-Agent': 'Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/58.0.3029.110 Safari/537.3',
}
url = "https://stockanalysis.com/ipos/2023/"
response = requests.get(url, headers=headers)

ipo_dfs = pd.read_html(response.text)

ipos_2023 = ipo_dfs[0]
ipos_2023.info()

# Get IPOs data from 2024
url = "https://stockanalysis.com/ipos/2024/"
response = requests.get(url, headers=headers)

ipo_dfs = pd.read_html(response.text)

ipos_2024 = ipo_dfs[0]
ipos_2024.info()    

# Concatenate into one df
stacked_ipos_df = pd.concat([ipos_2024, ipos_2023], ignore_index=True)
stacked_ipos_df.head(1)  

C:\Users\mmo990\AppData\Local\Temp\ipykernel_19408\4261671331.py:8: FutureWarning: Passing literal html to 'read_html' is deprecated and will be removed in a future version. To read from a literal string, wrap it in a 'StringIO' object.
  ipo_dfs = pd.read_html(response.text)


<class 'pandas.core.frame.DataFrame'>
RangeIndex: 154 entries, 0 to 153
Data columns (total 6 columns):
 #   Column        Non-Null Count  Dtype 
---  ------        --------------  ----- 
 0   IPO Date      154 non-null    object
 1   Symbol        154 non-null    object
 2   Company Name  154 non-null    object
 3   IPO Price     154 non-null    object
 4   Current       154 non-null    object
 5   Return        154 non-null    object
dtypes: object(6)
memory usage: 7.3+ KB
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 64 entries, 0 to 63
Data columns (total 6 columns):
 #   Column        Non-Null Count  Dtype 
---  ------        --------------  ----- 
 0   IPO Date      64 non-null     object
 1   Symbol        64 non-null     object
 2   Company Name  64 non-null     object
 3   IPO Price     64 non-null     object
 4   Current       64 non-null     object
 5   Return        64 non-null     object
dtypes: object(6)
memory usage: 3.1+ KB


C:\Users\mmo990\AppData\Local\Temp\ipykernel_19408\4261671331.py:17: FutureWarning: Passing literal html to 'read_html' is deprecated and will be removed in a future version. To read from a literal string, wrap it in a 'StringIO' object.
  ipo_dfs = pd.read_html(response.text)


IPO Date Symbol          Company Name IPO Price Current  Return
0  May 1, 2024    VIK  Viking Holdings Ltd.    $24.00  $28.65  19.38%

In [4]:
# Convert to datetime
stacked_ipos_df['IPO Date'] = pd.to_datetime(stacked_ipos_df['IPO Date'], format='%b %d, %Y')

In [5]:
# Get all OHLCV daily prices for all stocks with an "IPO date" before March 1, 2024
stacked_ipos_df = stacked_ipos_df[(stacked_ipos_df['IPO Date'] < '2024-03-01')]
stacked_ipos_df = stacked_ipos_df[stacked_ipos_df['Symbol'] != 'RYZB']
stacked_ipos_df

IPO Date Symbol                             Company Name IPO Price  \
33  2024-02-27   SMXT                SolarMax Technology, Inc.     $4.00   
34  2024-02-22   VHAI                    Vocodia Holdings Corp     $4.25   
35  2024-02-21   DYCQ         DT Cloud Acquisition Corporation    $10.00   
36  2024-02-16   CHRO             Chromocell Therapeutics Corp     $6.00   
37  2024-02-14   UMAC                   Unusual Machines, Inc.     $4.00   
..         ...    ...                                      ...       ...   
213 2023-01-25    QSG                     QuantaSing Group Ltd    $12.50   
214 2023-01-20   CVKD              Cadrenal Therapeutics, Inc.     $5.00   
215 2023-01-13   SKWD  Skyward Specialty Insurance Group, Inc.    $15.00   
216 2023-01-13   ISRL                 Israel Acquisitions Corp    $10.00   
217 2023-01-13   MGOL                          MGO Global Inc.     $5.00   

    Current   Return  
33   $10.34  158.50%  
34    $0.13  -96.86%  
35   $10.16    1.60%  
36    $1.84  -69.33%  
37    $1.05  -73.25%  
..      ...      ...  
213   $3.19  -74.48%  
214   $0.48  -90.40%  
215  $37.61  150.73%  
216  $10.93    9.30%  
217   $0.22  -95.50%  

[184 rows x 6 columns]

In [6]:
# Get info on ticker name changes
headers = {
    'User-Agent': 'Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/58.0.3029.110 Safari/537.3',
}
url = "https://stockanalysis.com/actions/changes/"
response = requests.get(url, headers=headers)

tickr_dfs = pd.read_html(response.text)

C:\Users\mmo990\AppData\Local\Temp\ipykernel_19408\2690590118.py:8: FutureWarning: Passing literal html to 'read_html' is deprecated and will be removed in a future version. To read from a literal string, wrap it in a 'StringIO' object.
  tickr_dfs = pd.read_html(response.text)


In [77]:
# Update tickers in stacked_ipos_df
# Merge the DataFrames on 'Symbol' and 'Old'
merged_df = pd.merge(stacked_ipos_df, tickr_dfs[0], left_on='Symbol', right_on='Old', how='left')

# Update 'Symbol' column where 'New' is not null
merged_df['Symbol'] = merged_df['New'].fillna(merged_df['Symbol'])

# Drop unnecessary columns
merged_df.drop(['Old', 'New', 'Date', 'New Company Name'], axis=1, inplace=True)

# Output the updated DataFrame
print(merged_df)

      IPO Date Symbol                             Company Name IPO Price  \
0   2024-02-27   SMXT                SolarMax Technology, Inc.     $4.00   
1   2024-02-22   VHAI                    Vocodia Holdings Corp     $4.25   
2   2024-02-21   DYCQ         DT Cloud Acquisition Corporation    $10.00   
3   2024-02-16   CHRO             Chromocell Therapeutics Corp     $6.00   
4   2024-02-14   UMAC                   Unusual Machines, Inc.     $4.00   
..         ...    ...                                      ...       ...   
179 2023-01-25    QSG                     QuantaSing Group Ltd    $12.50   
180 2023-01-20   CVKD              Cadrenal Therapeutics, Inc.     $5.00   
181 2023-01-13   SKWD  Skyward Specialty Insurance Group, Inc.    $15.00   
182 2023-01-13   ISRL                 Israel Acquisitions Corp    $10.00   
183 2023-01-13   MGOL                          MGO Global Inc.     $5.00   

    Current   Return  
0    $10.34  158.50%  
1     $0.13  -96.86%  
2    $10.16    1.6

In [15]:
# Get data for tickers in column 'Symbol' from Yahoo Finance
tickers = merged_df['Symbol'].to_list()
data = yf.download(tickers, start='2023-01-13')

[*********************100%%**********************]  184 of 184 completed


In [18]:
data_adj_close = data['Adj Close']

In [78]:
# Make new column name index for df with a column for each growth day up to 30 days
column_names = [f'growth_future_{i}d' for i in range(1, 31)]
column_names = merged_df.columns.tolist() + column_names 
merged_df = merged_df.reindex(column_names, axis=1)

In [79]:
# Iterate over tickers in IPO df merged_df
for index, row in merged_df.iterrows():
    company = row['Symbol']
    ipo_date = row['IPO Date']
    adj_close_ini = data_adj_close[company].loc[ipo_date]
    specific_row_index = data_adj_close[company].index.get_loc(ipo_date)
    # Check if adj_close_ini is NaN
    if np.isnan(adj_close_ini):
        # Find the next non-NaN value in data_adj_close[company] following ipo_date
        new_date_index = data_adj_close[company].loc[ipo_date:].dropna().index[0]
        next_valid_adj_close_value = data_adj_close[company].loc[new_date_index]       
        
        if next_valid_adj_close_value is not None:
            adj_close_ini = next_valid_adj_close_value
            specific_row_index = data_adj_close[company].index.get_loc(new_date_index)
        else:
            # Handle case where no valid index is found
            print(f"No valid adj close value found for {company} after {ipo_date}")
    if len(data_adj_close[company].dropna()) < 30:
        for i in range(1, len(data_adj_close[company].dropna())):
            merged_df[f'growth_future_{i}d'].iloc[index] = ((data_adj_close[company].iloc[specific_row_index+i] - adj_close_ini) / adj_close_ini) * 100
    else:
        for i in range(1, 31):
            merged_df[f'growth_future_{i}d'].iloc[index] = ((data_adj_close[company].iloc[specific_row_index+i] - adj_close_ini) / adj_close_ini) * 100


C:\Users\mmo990\AppData\Local\Temp\ipykernel_19408\3396038313.py:24: FutureWarning: ChainedAssignmentError: behaviour will change in pandas 3.0!
You are setting values through chained assignment. Currently this works in certain cases, but when using Copy-on-Write (which will become the default behaviour in pandas 3.0) this will never work to update the original DataFrame or Series, because the intermediate object on which we are setting values will behave as a copy.
A typical example is when you are setting values in a column of a DataFrame, like:

df["col"][row_indexer] = value

Use `df.loc[row_indexer, "col"] = values` instead, to perform the assignment in a single step and ensure this keeps updating the original `df`.

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

  merged_df[f'growth_future_{i}d'].iloc[index] = ((data_adj_close[company].iloc[specific_row_index+i] - adj_close_ini) / adj_clo

In [84]:
e = merged_df.describe()

In [91]:
e.loc['75%'][1:]

growth_future_1d     1.701413
growth_future_2d     2.153448
growth_future_3d     1.182495
growth_future_4d      1.45565
growth_future_5d     0.951695
growth_future_6d     0.714681
growth_future_7d     0.689994
growth_future_8d     0.812672
growth_future_9d     1.232588
growth_future_10d     0.90112
growth_future_11d     1.11552
growth_future_12d     1.60157
growth_future_13d    1.867563
growth_future_14d    1.970587
growth_future_15d    1.628372
growth_future_16d     1.41903
growth_future_17d    1.133038
growth_future_18d    1.527566
growth_future_19d    1.816314
growth_future_20d     1.51452
growth_future_21d    1.420901
growth_future_22d    3.875439
growth_future_23d    3.228464
growth_future_24d    4.307462
growth_future_25d     2.69723
growth_future_26d    2.825569
growth_future_27d    3.653667
growth_future_28d    4.024465
growth_future_29d    2.636188
growth_future_30d    2.371804
Name: 75%, dtype: object

In [95]:
max_75_growth = e.loc['75%'][1:].max()
max_75_growth_index = e.loc['75%'][1:].idxmax()
print(max_75_growth_index)

growth_future_24d


In [ ]:
# To be used for home assignment: 'You can notice a bump in the price after the IPO? And after that the price goes down
# You're asked to design a simple strategy to buy and hold for X days (at 'Adj.Close' price, no fees)
# Find an optimal X between 1 and 30, that delivers you a MAX mean return on ALL 2023 IPOs?
# Write down the answer X (a number between 1 and 30)

# What is the distribution of other returns 25-50-75% quantiles? Compare mean and median returns for 2023 (median may be more robust),
  # are you losing money in 25% cases (if 25% quantile returns is < 0)
  # Try the same X for all deals in 2024.  How the mean return in 2024 (out of sample data) is different from 2023 data?

# REDDIT - recent IPO
# https://finance.yahoo.com/quote/RDDT/
reddit = yf.download(tickers = "RDDT",
                     period = "max",
                     interval = "1d")

reddit.tail()

# Question 3

In [134]:
# Define the list of stocks
US_STOCKS = ['MSFT', 'AAPL', 'GOOG', 'NVDA', 'AMZN', 'META', 'BRK-B', 'LLY', 'AVGO', 'V', 'JPM']
EU_STOCKS = ['NVO','MC.PA', 'ASML', 'RMS.PA', 'OR.PA', 'SAP', 'ACN', 'TTE', 'SIE.DE', 'IDEXY','CDI.PA']
INDIA_STOCKS = ['RELIANCE.NS','TCS.NS','HDB','BHARTIARTL.NS','IBN','SBIN.NS','LICI.NS','INFY','ITC.NS','HINDUNILVR.NS','LT.NS']
LARGEST_STOCKS = US_STOCKS + EU_STOCKS + INDIA_STOCKS

NEW_US = ['TSLA','WMT','XOM','UNH','MA','PG','JNJ','MRK','HD','COST','ORCL']
NEW_EU = ['PRX.AS','CDI.PA','AIR.PA','SU.PA','ETN','SNY','BUD','DTE.DE','ALV.DE','MDT','AI.PA','EL.PA']
NEW_INDIA = ['BAJFINANCE.NS','MARUTI.NS','HCLTECH.NS','TATAMOTORS.NS','SUNPHARMA.NS','ONGC.NS','ADANIENT.NS','ADANIENT.NS','NTPC.NS','KOTAKBANK.NS','TITAN.NS']
LARGE_STOCKS = NEW_EU + NEW_US + NEW_INDIA

# Combine the lists
ALL_STOCKS = LARGEST_STOCKS + LARGE_STOCKS

# Download OHLCV data for the specified stocks
data = yf.download(ALL_STOCKS, start="2013-11-01", end="2023-12-31")


[*********************100%%**********************]  65 of 65 completed


In [140]:
# Calculate growth_7d for each stock and each day
data_growth_7d  = data['Adj Close'] / data['Adj Close'].shift(7)
data_growth_7d_t = data_growth_7d.T
data_growth_7d_t = data_growth_7d_t.loc[:, '2014-01-01':]
data_growth_7d_t


Date         2014-01-01  2014-01-02  2014-01-03  2014-01-06  2014-01-07  \
Ticker                                                                    
AAPL                NaN    0.970250    0.952984    0.964586    0.964202   
ACN                 NaN    0.994850    1.001107    0.980402    0.988001   
ADANIENT.NS    1.035646    0.940516    0.924953    0.934210    0.887890   
AI.PA               NaN    1.010308    1.012968         NaN    0.961237   
AIR.PA              NaN    1.011447    1.004452         NaN    0.994132   
...                 ...         ...         ...         ...         ...   
TTE                 NaN    1.000666    0.990035    0.985899    0.972585   
UNH                 NaN    1.002959    1.013085    0.991850    1.024367   
V                   NaN    1.013667    1.011110    0.998319    1.008376   
WMT                 NaN    1.013356    1.008204    0.997704    0.999745   
XOM                 NaN    1.012588    1.002923    0.987710    0.995666   

Date         2014-01-08  2014-01-09  2014-01-10  2014-01-13  2014-01-14  ...  \
Ticker                                                                   ...   
AAPL           0.980055    0.956329         NaN    0.968543    1.010000  ...   
ACN            1.001097    1.008879         NaN    0.999137    1.006757  ...   
ADANIENT.NS    0.901972    0.935428    0.896558    0.921481    0.983491  ...   
AI.PA          0.966911    0.955448         NaN    0.976424    0.965633  ...   
AIR.PA         0.993181    0.980290         NaN    0.986384    0.994681  ...   
...                 ...         ...         ...         ...         ...  ...   
TTE            0.964338    0.961481         NaN    0.974863    0.999496  ...   
UNH            1.011234    1.010359         NaN    0.991552    0.985619  ...   
V              1.005930    0.996542         NaN    0.990453    1.006737  ...   
WMT            0.989826    0.992375         NaN    0.982005    0.991227  ...   
XOM            1.004287    0.985770         NaN    0.987970    0.996081  ...   

Date         2023-12-15  2023-12-18  2023-12-19  2023-12-20  2023-12-21  \
Ticker                                                                    
AAPL           1.027298    1.008339    1.006285    1.008541    0.999846   
ACN            1.026058    1.020143    1.012692    0.991791    1.016112   
ADANIENT.NS    1.037397    1.032368    1.042202    0.974806    0.979739   
AI.PA          1.014528    1.011961    1.006845    1.004756    0.991251   
AIR.PA         1.008821    1.005926    0.986321    0.968939    0.970844   
...                 ...         ...         ...         ...         ...   
TTE            1.032233    1.033888    1.019979    1.010071    1.031363   
UNH            0.966499    0.960384    0.953199    0.948959    0.952650   
V              1.014708    1.009968    1.016618    1.002300    0.999923   
WMT            0.995243    1.016463    1.030956    1.016332    1.022727   
XOM            1.018061    1.032819    1.034555    1.016563    1.037532   

Date         2023-12-22  2023-12-26  2023-12-27  2023-12-28  2023-12-29  
Ticker                                                                   
AAPL           0.977975    0.974459    0.977628    0.988208    0.977607  
ACN            1.031457    1.031220    1.028098    1.028492    1.027525  
ADANIENT.NS    0.976800    0.990118    0.950381    0.942730    0.968619  
AI.PA          0.990617         NaN    1.004773    1.001250    0.997734  
AIR.PA         0.979902         NaN    0.999283    1.003592    0.999285  
...                 ...         ...         ...         ...         ...  
TTE            1.020877    1.017862    1.033318    0.999735    1.004087  
UNH            0.947724    0.973402    0.984316    0.996866    1.004637  
V              0.984945    1.001662    1.003488    1.007857    1.001385  
WMT            1.016878    1.027864    1.033652    1.016777    1.013631  
XOM            1.030227    1.005513    1.007532    0.985637    0.970774  

[65 rows x 2595 columns]

In [141]:
# Function to add string that either says 'Large' or 'Largest'
def assign_label(index_str):
    if index_str in LARGEST_STOCKS:
        return 'LARGEST'
    elif index_str in LARGE_STOCKS:
        return 'LARGE'
    else:
        return None  # or any default value if needed

data_growth_7d_t['ticker_category'] = data_growth_7d_t.index.to_series().apply(assign_label)


In [146]:
# Calculate the mean for each group
mean_grouped = data_growth_7d_t.groupby('ticker_category').mean()

# Count the occurrences when one mean is higher than the other
count_higher_large = (mean_grouped.loc['LARGE'] > mean_grouped.loc['LARGEST']).sum()  # Count occurrences when mean of 'LARGE' is higher
count_higher_largest = (mean_grouped.loc['LARGEST'] > mean_grouped.loc['LARGE']).sum()  # Count occurrences when mean of 'LARGEST' is higher


In [152]:
# Calculate percentage number of days when the LARGE GROUP (new smaller stocks) outperforms the LARGEST GROUP
count_higher_large/(len(data_growth_7d_t.columns) - 1) * 100

46.4354527938343

# Question 4
## What's the total gross profit (in THOUSANDS of $) you'll get from trading on CCI (no fees assumption)?


In [68]:
%store -r m16

In [69]:
# Set the date as index
m16 = m16.reset_index().set_index('Date')

In [70]:
# Only select data from 2014-01-01 to 2023-12-31
m16 = m16[(m16.index > '2014-01-01') & (m16.index < '2023-12-31')]

In [163]:
# Initialize gross profit
gross_profit = 0

# Iterate over each row in the DataFrame
for index, row in m16.iterrows():
    # Check if CCI is greater than 200
    if row['cci'] > 200:
        # Only perform calculations if the date is before 2023-12-22
        if index < datetime.strptime('2023-12-22', '%Y-%m-%d'):
            # Get the ticker corresponding to the current row
            ticker = row['Ticker']
            # Calculate the investment amount
            investment = 1000
            # Find the date to sell after 5 trading days
            sell_date = index + pd.DateOffset(days=7)
            # Calculate the profit/loss based on the Adj.Close price after 5 days
            ticker_df = m16[m16['Ticker'] == ticker]
            # Check if sell date is in index
            while sell_date.strftime('%Y-%m-%d') not in ticker_df.index:
                sell_date += timedelta(days=1)
            sell_date = sell_date.strftime('%Y-%m-%d')
            profit = (ticker_df.loc[sell_date, 'Adj Close_x'] - row['Adj Close_x']) * (1000/row['Adj Close_x'])
            # Add profit/loss to gross profit
            gross_profit += profit
        else:
            break


# Convert gross profit to thousands and round to the nearest integer
gross_profit_thousands = round(gross_profit / 1000)


In [165]:
gross_profit_thousands

3

# Question 5
You've seen in the first questions that the median and average investments are negative in IPOs, and you can't blindly invest in all deals.

How would you correct/refine the approach? Briefly describe the steps and the data you'll try to get (it should be generally feasible to do it from public sources - no access to internal data of companies)?

E.g. (some ideas) Do you want to focus on the specific vertical? Do you want to build a smart comparison vs. existing stocks on the market? Or you just will want to get some features (which features?) like total number of people in a company to find a segment of "successful" IPOs?


I would focus on a specific vertical that I had knowledge on or a big interest to get knowledge, and one that I thought was healthy and had growth potential. This would allow me to be familiar with important managers in the field and have an idea of who the team leading the company is. I would read the prospectus of the company and look up as much information that is available on them as possible. I think a smart comparison vs exisitng stocks on the market in that vertical would also be smart.